In [ ]:
from google.colab import drive
drive.mount("/content/drive")

Mounted at /content/drive


In [ ]:
!nvidia-smi

Tue Dec  6 21:14:54 2022       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 460.32.03    Driver Version: 460.32.03    CUDA Version: 11.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla T4            Off  | 00000000:00:04.0 Off |                    0 |
| N/A   53C    P0    27W /  70W |      0MiB / 15109MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [ ]:
!pip install transformers

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 5.8 MB 5.0 MB/s 
     |████████████████████████████████| 7.6 MB 84.9 MB/s 
     |████████████████████████████████| 182 kB 84.8 MB/s 


In [ ]:
import torch
import torch.nn as nn
import pandas as pd
import numpy as np
import shutil
import sys

In [ ]:
train_path = "/content/drive/MyDrive/Data/FullLitCovid/train.tsv"
test_path = "/content/drive/MyDrive/Data/FullLitCovid/test.tsv"
val_path="/content/drive/MyDrive/Data/FullLitCovid/val.tsv"
eval_path="/content/drive/MyDrive/Data/cord19_test.tsv"

In [ ]:
train_df = pd.read_csv(train_path,sep='\t',header=None,dtype={0:str,1:str})
test_df = pd.read_csv(test_path,sep='\t',header=None,dtype={0:str,1:str})
val_df=pd.read_csv(val_path,sep='\t',header=None,dtype={0:str,1:str})
eval_df=pd.read_csv(eval_path,sep='\t',header=None,dtype={0:str,1:str})

In [ ]:
print(len(train_df.index))
print(len(val_df.index))
print(len(test_df.index))
print(len(eval_df.index))

24718
3532
7063
100


In [ ]:
train_df.head()

0                                                  1
0  01100000  structural conservation among variants sars-co...
1  00001000  effective management idiopathic intracranial h...
2  00001000  `` 's whole different atmosphere '' qualitativ...
3  01100000  modification spike protein vaccines enveloped ...
4  00001010  analysis prediction covid-19 outbreak pakistan...

In [ ]:
target_list = ['diagnosis', 'treatment', 'mechanism', 'transmission','prevention', 'case_report','forecasting','general']

In [ ]:
def addCol(df,target_list):
  for label in target_list:
    df[label]=0
  return df

In [ ]:
train_df=addCol(train_df,target_list)
test_df=addCol(test_df,target_list)
val_df=addCol(val_df,target_list)
eval_df=addCol(eval_df,target_list)


In [ ]:
def vector_labels(df,target_list):
  print(df.index)
  for ind in df.index:
    #label = df[0][ind]
    label = df[0][ind]
    #print(label)
    for i,cat in enumerate(label):
      if cat == '1':
        #print(i)
        df[target_list[i]][ind]=1
  return df


In [ ]:
train_df=vector_labels(train_df,target_list)
test_df=vector_labels(test_df,target_list)
val_df=vector_labels(val_df,target_list)
eval_df=vector_labels(eval_df,target_list)

RangeIndex(start=0, stop=24718, step=1)


<ipython-input-12-db4a9e98be24>:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[target_list[i]][ind]=1


RangeIndex(start=0, stop=7063, step=1)
RangeIndex(start=0, stop=3532, step=1)
RangeIndex(start=0, stop=100, step=1)


In [ ]:
eval_df

0                                                  1  diagnosis  \
0   00010000  the 1918–1919 influenza pandemic in england an...          0   
1   00000001  buried treasure : evolutionary perspectives on...          0   
2   01100000  polyether ionophores : broad-spectrum and prom...          0   
3   10000000  stillbirth during infection with middle east r...          1   
4   01000000  approved antiviral drugs over the past 50 year...          0   
..       ...                                                ...        ...   
95  00001000  proposed calfhood immunization program for the...          0   
96  10000000  risk of bacterial coinfections in febrile infa...          1   
97  00100000  early days : genomics and human responses to i...          0   
98  00100000  autophagic machinery activated by dengue virus...          0   
99  10100000  development of a multiplex one step rt-pcr tha...          1   

    treatment  mechanism  transmission  prevention  case_report  forecasting  \
0           0          0             1           0            0            0   
1           0          0             0           0            0            0   
2           1          1             0           0            0            0   
3           0          0             0           0            0            0   
4           1          0             0           0            0            0   
..        ...        ...           ...         ...          ...          ...   
95          0          0             0           1            0            0   
96          0          0             0           0            0            0   
97          0          1             0           0            0            0   
98          0          1             0           0            0            0   
99          0          1             0           0            0            0   

    general  
0         0  
1         1  
2         0  
3         0  
4         0  
..      ...  
95        0  
96        0  
97        0  
98        0  
99        0  

[100 rows x 10 columns]

In [ ]:
test_df

0                                                  1  diagnosis  \
0     00001000  covid-19 impacted immunisation service deliver...          0   
1     11000000  new insights seriousness acute myocardial inju...          1   
2     00001000  guidelines adaptation covid-19 outbreak manage...          0   
3     00001000  implementing strategies workplace level increa...          0   
4     00001000  global healthcare resource efficiency manageme...          0   
...        ...                                                ...        ...   
7058  10010000  sars-cov-2 big seroprevalence data pakistan he...          1   
7059  00001000  effect home-based prehabilitation enhanced rec...          0   
7060  11100000  cardiovascular system covid-19 simply viewer l...          1   
7061  01000000  precision medicine covid-19 il-1beta potential...          0   
7062  10000000  comparative analysis diagnostic performance fi...          1   

      treatment  mechanism  transmission  prevention  case_report  \
0             0          0             0           1            0   
1             1          0             0           0            0   
2             0          0             0           1            0   
3             0          0             0           1            0   
4             0          0             0           1            0   
...         ...        ...           ...         ...          ...   
7058          0          0             1           0            0   
7059          0          0             0           1            0   
7060          1          1             0           0            0   
7061          1          0             0           0            0   
7062          0          0             0           0            0   

      forecasting  general  
0               0        0  
1               0        0  
2               0        0  
3               0        0  
4               0        0  
...           ...      ...  
7058            0        0  
7059            0        0  
7060            0        0  
7061            0        0  
7062            0        0  

[7063 rows x 10 columns]

In [ ]:
val_df

0                                                  1  diagnosis  \
0     00011010  mathematical modelling optimal cost-effective ...          0   
1     11000000  different pattern second outbreak covid-19 mar...          1   
2     00001000  covid-19 implications cornea donation activity...          0   
3     00001000  low incidence sars-cov-2 infections healthcare...          0   
4     00001010  homogenous mixing network approximations discr...          0   
...        ...                                                ...        ...   
3527  00100000  fast microwave heating-based one-step synthesi...          0   
3528  00001000  pattern visits metropolitan emergency departme...          0   
3529  00001000  invited commentary 'evidence based management ...          0   
3530  01100000  risk covid-19-related hospitalization severe o...          0   
3531  01000000  physicians opinions necessity covid-19 vaccina...          0   

      treatment  mechanism  transmission  prevention  case_report  \
0             0          0             1           1            0   
1             1          0             0           0            0   
2             0          0             0           1            0   
3             0          0             0           1            0   
4             0          0             0           1            0   
...         ...        ...           ...         ...          ...   
3527          0          1             0           0            0   
3528          0          0             0           1            0   
3529          0          0             0           1            0   
3530          1          1             0           0            0   
3531          1          0             0           0            0   

      forecasting  general  
0               1        0  
1               0        0  
2               0        0  
3               0        0  
4               1        0  
...           ...      ...  
3527            0        0  
3528            0        0  
3529            0        0  
3530            0        0  
3531            0        0  

[3532 rows x 10 columns]

In [ ]:
train_df.drop(labels=[0], axis=1, inplace=True)
test_df.drop(labels=[0], axis=1, inplace=True)
val_df.drop(labels=[0], axis=1, inplace=True)
eval_df.drop(labels=[0], axis=1, inplace=True)

In [ ]:
len(val_df.index)

3532

In [ ]:
# hyperparameters
MAX_LEN = 512
TRAIN_BATCH_SIZE = 6
TEST_BATCH_SIZE = 6
VALID_BATCH_SIZE = 6
EVAL_BATCH_SIZE=6
EPOCHS = 10
LEARNING_RATE = 1e-5

In [ ]:
from transformers import BertTokenizer, BertModel

In [ ]:
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

Downloading:   0%|          | 0.00/232k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/28.0 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/570 [00:00<?, ?B/s]

In [ ]:
class CustomDataset(torch.utils.data.Dataset):

    def __init__(self, df, tokenizer, max_len):
        self.tokenizer = tokenizer
        self.df = df
        self.title = df[1]
        self.targets = self.df[target_list].values
        self.max_len = max_len

    def __len__(self):
        return len(self.title)

    def __getitem__(self, index):
        title = str(self.title[index])
        title = " ".join(title.split())

        inputs = self.tokenizer.encode_plus(
            title,
            None,
            add_special_tokens=True,
            max_length=self.max_len,
            padding='max_length',
            return_token_type_ids=True,
            truncation=True,
            return_attention_mask=True,
            return_tensors='pt'
        )

        return {
            'input_ids': inputs['input_ids'].flatten(),
            'attention_mask': inputs['attention_mask'].flatten(),
            'token_type_ids': inputs["token_type_ids"].flatten(),
            'targets': torch.FloatTensor(self.targets[index])
        }

In [ ]:
train_dataset = CustomDataset(train_df, tokenizer, MAX_LEN)
valid_dataset = CustomDataset(val_df, tokenizer, MAX_LEN)

In [ ]:
train_data_loader = torch.utils.data.DataLoader(train_dataset, 
    batch_size=TRAIN_BATCH_SIZE,
    shuffle=True,
    num_workers=0  
)

val_data_loader = torch.utils.data.DataLoader(valid_dataset, 
    batch_size=VALID_BATCH_SIZE,
    shuffle=False,
    num_workers=0
)

In [ ]:
device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')

In [ ]:
device

device(type='cuda')

In [ ]:
def load_ckp(checkpoint_fpath, model, optimizer):
    """
    checkpoint_path: path to save checkpoint
    model: model that we want to load checkpoint parameters into       
    optimizer: optimizer we defined in previous training
    """
    # load check point
    checkpoint = torch.load(checkpoint_fpath)
    # initialize state_dict from checkpoint to model
    model.load_state_dict(checkpoint['state_dict'])
    # initialize optimizer from checkpoint to optimizer
    optimizer.load_state_dict(checkpoint['optimizer'])
    # initialize valid_loss_min from checkpoint to valid_loss_min
    valid_loss_min = checkpoint['valid_loss_min']
    # return model, optimizer, epoch value, min validation loss 
    return model, optimizer, checkpoint['epoch'], valid_loss_min.item()

def save_ckp(state, is_best, checkpoint_path, best_model_path):
    """
    state: checkpoint we want to save
    is_best: is this the best checkpoint; min validation loss
    checkpoint_path: path to save checkpoint
    best_model_path: path to save best model
    """
    f_path = checkpoint_path
    # save checkpoint data to the path given, checkpoint_path
    torch.save(state, f_path)
    # if it is a best model, min validation loss
    if is_best:
        best_fpath = best_model_path
        # copy that checkpoint file to best path given, best_model_path
        shutil.copyfile(f_path, best_fpath)

In [ ]:
import torch
torch.cuda.empty_cache()
class BERTClass(torch.nn.Module):
    def __init__(self):
        super(BERTClass, self).__init__()
        self.bert_model = BertModel.from_pretrained('bert-base-uncased', return_dict=True)
        self.dropout = torch.nn.Dropout(0.3)
        self.linear = torch.nn.Linear(768, 8)
    
    def forward(self, input_ids, attn_mask, token_type_ids):
        output = self.bert_model(
            input_ids, 
            attention_mask=attn_mask, 
            token_type_ids=token_type_ids
        )
        output_dropout = self.dropout(output.pooler_output)
        output = self.linear(output_dropout)
        return output

model = BERTClass()
model.to(device)

Downloading:   0%|          | 0.00/440M [00:00<?, ?B/s]

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertModel: ['cls.predictions.transform.dense.bias', 'cls.seq_relationship.bias', 'cls.seq_relationship.weight', 'cls.predictions.decoder.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.dense.weight']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


BERTClass(
  (bert_model): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(30522, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0): BertLayer(
          (attention): BertAttention(
            (self): BertSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=Tr

In [ ]:
def loss_fn(outputs, targets):
    return torch.nn.BCEWithLogitsLoss()(outputs, targets)

optimizer = torch.optim.Adam(params =  model.parameters(), lr=LEARNING_RATE)

In [ ]:
val_targets=[]
val_outputs=[]

In [ ]:
import torch
torch.cuda.empty_cache()

def train_model(n_epochs, training_loader, validation_loader, model, 
                optimizer, checkpoint_path, best_model_path):
   
  # initialize tracker for minimum validation loss
  valid_loss_min = np.Inf
   
 
  for epoch in range(1, n_epochs+1):
    train_loss = 0
    valid_loss = 0

    model.train()
    print('############# Epoch {}: Training Start   #############'.format(epoch))
    for batch_idx, data in enumerate(training_loader):
        #print('yyy epoch', batch_idx)
        ids = data['input_ids'].to(device, dtype = torch.long)
        mask = data['attention_mask'].to(device, dtype = torch.long)
        token_type_ids = data['token_type_ids'].to(device, dtype = torch.long)
        targets = data['targets'].to(device, dtype = torch.float)

        outputs = model(ids, mask, token_type_ids)

        optimizer.zero_grad()
        loss = loss_fn(outputs, targets)
        #if batch_idx%5000==0:
         #   print(f'Epoch: {epoch}, Training Loss:  {loss.item()}')
        
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()
        #print('before loss data in training', loss.item(), train_loss)
        train_loss = train_loss + ((1 / (batch_idx + 1)) * (loss.item() - train_loss))
        #print('after loss data in training', loss.item(), train_loss)
        #print("The targets")
        #print(targets)
        #print("The outputs")
        #print(outputs)
    
    print('############# Epoch {}: Training End     #############'.format(epoch))
    
    print('############# Epoch {}: Validation Start   #############'.format(epoch))
    ######################    
    # validate the model #
    ######################
    model.eval()
   
    with torch.no_grad():
      for batch_idx, data in enumerate(validation_loader, 0):
            ids = data['input_ids'].to(device, dtype = torch.long)
            mask = data['attention_mask'].to(device, dtype = torch.long)
            token_type_ids = data['token_type_ids'].to(device, dtype = torch.long)
            targets = data['targets'].to(device, dtype = torch.float)
            outputs = model(ids, mask, token_type_ids)
            #print("The targets")
            #print(targets)
            #print("The outputs")
            #print(outputs)
            loss = loss_fn(outputs, targets)
            valid_loss = valid_loss + ((1 / (batch_idx + 1)) * (loss.item() - valid_loss))
            val_targets.extend(targets.cpu().detach().numpy().tolist())
            val_outputs.extend(torch.sigmoid(outputs).cpu().detach().numpy().tolist())

      print('############# Epoch {}: Validation End     #############'.format(epoch))
      # calculate average losses
      #print('before cal avg train loss', train_loss)
      train_loss = train_loss/len(training_loader)
      valid_loss = valid_loss/len(validation_loader)
      # print training/validation statistics 
      print('Epoch: {} \tAvgerage Training Loss: {:.6f} \tAverage Validation Loss: {:.6f}'.format(
            epoch, 
            train_loss,
            valid_loss
            ))
      
      # create checkpoint variable and add important data
      checkpoint = {
            'epoch': epoch + 1,
            'valid_loss_min': valid_loss,
            'state_dict': model.state_dict(),
            'optimizer': optimizer.state_dict()
      }
        
        # save checkpoint
      save_ckp(checkpoint, False, checkpoint_path, best_model_path)
        
      ## TODO: save the model if validation loss has decreased
      if valid_loss <= valid_loss_min:
        print('Validation loss decreased ({:.6f} --> {:.6f}).  Saving model ...'.format(valid_loss_min,valid_loss))
        # save checkpoint as best model
        save_ckp(checkpoint, True, checkpoint_path, best_model_path)
        valid_loss_min = valid_loss

    print('############# Epoch {}  Done   #############\n'.format(epoch))

  return model

In [ ]:
ckpt_path = "/content/drive/MyDrive/Data/curr_ckpt1"
best_model_path = "/content/drive/MyDrive/Data/best_model1.pt"

In [ ]:

import torch
torch.cuda.empty_cache()  
trained_model = train_model(EPOCHS, train_data_loader, val_data_loader, model, optimizer, ckpt_path, best_model_path)

############# Epoch 1: Training Start   #############
############# Epoch 1: Training End     #############
############# Epoch 1: Validation Start   #############
############# Epoch 1: Validation End     #############
Epoch: 1 	Avgerage Training Loss: 0.000023 	Average Validation Loss: 0.000142
Validation loss decreased (inf --> 0.000142).  Saving model ...
############# Epoch 1  Done   #############

############# Epoch 2: Training Start   #############
############# Epoch 2: Training End     #############
############# Epoch 2: Validation Start   #############
############# Epoch 2: Validation End     #############
Epoch: 2 	Avgerage Training Loss: 0.000017 	Average Validation Loss: 0.000138
Validation loss decreased (0.000142 --> 0.000138).  Saving model ...
############# Epoch 2  Done   #############

############# Epoch 3: Training Start   #############
############# Epoch 3: Training End     #############
############# Epoch 3: Validation Start   #############
############# Epo

KeyboardInterrupt: ignored

In [ ]:
print(val_targets)
print(val_outputs)

[[0.0, 0.0, 0.0, 1.0, 1.0, 0.0, 1.0, 0.0], [1.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0], [0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0], [0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0], [0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 1.0, 0.0], [0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0], [0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0], [1.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0], [0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0], [0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0], [0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0], [0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0], [0.0, 1.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0], [1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0], [1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0], [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0], [0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0], [0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0], [0.0, 1.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0], [0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0], [0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0], [0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0], [1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0], [0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.

In [ ]:
print(len(val_targets))
print(len(val_outputs))

10596
10596


In [ ]:
def thresholded_output_trans(output):
    y_pred = output
    for sublst in y_pred:
      for i, val in enumerate(sublst):
        sublst[i] = round(val)
    return y_pred

val_outputs = thresholded_output_trans(val_outputs)
val_targets = thresholded_output_trans(val_targets)
print(val_outputs )
print(val_targets )

[[0, 0, 0, 1, 1, 0, 1, 0], [1, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 1, 0, 0, 0], [1, 0, 0, 0, 1, 0, 0, 0], [0, 0, 0, 0, 0, 0, 1, 0], [0, 0, 0, 0, 0, 1, 0, 0], [0, 0, 0, 0, 1, 0, 0, 0], [1, 1, 0, 0, 0, 0, 0, 0], [0, 1, 0, 0, 0, 0, 0, 0], [1, 1, 0, 0, 0, 0, 0, 0], [0, 1, 0, 0, 0, 0, 0, 0], [0, 0, 1, 0, 0, 0, 0, 0], [0, 1, 1, 0, 0, 0, 0, 0], [1, 0, 0, 0, 0, 0, 0, 0], [1, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 1, 0], [0, 0, 0, 0, 1, 0, 0, 0], [0, 0, 0, 0, 1, 0, 0, 0], [0, 1, 1, 0, 0, 0, 0, 0], [1, 1, 0, 0, 0, 0, 0, 0], [0, 0, 0, 1, 1, 0, 0, 0], [0, 0, 0, 0, 1, 0, 0, 0], [1, 0, 0, 0, 0, 0, 0, 0], [0, 1, 0, 0, 0, 0, 0, 0], [1, 1, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 1, 0, 0, 0], [1, 0, 0, 0, 0, 0, 0, 0], [1, 1, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 1, 0, 0, 0], [0, 1, 1, 0, 0, 0, 0, 0], [0, 0, 0, 0, 1, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 1, 1, 0, 0, 0, 0, 0], [0, 0, 0, 0, 1, 0, 0, 0], [0, 1, 1, 0, 0, 0, 0, 0], [0, 0, 0, 0, 1, 0, 0, 0], [0, 1, 1, 0, 0, 0, 0, 0], [0, 0, 1, 0, 0, 0, 0, 0], [0, 0, 0, 0

In [ ]:
from sklearn import metrics
from sklearn.metrics import ConfusionMatrixDisplay
from sklearn.metrics import confusion_matrix


print(metrics.accuracy_score(val_targets, val_outputs),metrics.f1_score(val_targets, val_outputs, average='micro'))

0.8038882597206493 0.9091659785301403


In [ ]:
test_dataset = CustomDataset(test_df, tokenizer, MAX_LEN)

In [ ]:

test_data_loader = torch.utils.data.DataLoader(test_dataset, 
    batch_size=TEST_BATCH_SIZE,
    shuffle=True,
    num_workers=0
)

test_targets=[]
test_outputs=[]

In [ ]:
print('############# Test Start   #############')
    ######################    
    # validate the model #
    ######################

model.eval()
   
with torch.no_grad():
  for batch_idx, data in enumerate(test_data_loader, 0):
    ids = data['input_ids'].to(device, dtype = torch.long)
    mask = data['attention_mask'].to(device, dtype = torch.long)
    token_type_ids = data['token_type_ids'].to(device, dtype = torch.long)
    targets = data['targets'].to(device, dtype = torch.float)
    outputs = model(ids, mask, token_type_ids)

    loss = loss_fn(outputs, targets)
    #valid_loss = valid_loss + ((1 / (batch_idx + 1)) * (loss.item() - valid_loss))
    test_targets.extend(targets.cpu().detach().numpy().tolist())
    test_outputs.extend(torch.sigmoid(outputs).cpu().detach().numpy().tolist())



print('############# Test End     #############')

############# Test Start   #############
############# Test End     #############


In [ ]:
print(test_targets)
print(test_outputs)

[[0.0, 1.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0], [0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0], [1.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0], [1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0], [0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0], [1.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0], [0.0, 1.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0], [0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0], [1.0, 1.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0], [1.0, 1.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0], [0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0], [0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0], [0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0], [0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0], [0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0], [1.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0], [0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0], [0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0], [1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0], [0.0, 1.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0], [1.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0], [0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0], [0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0], [0.0, 0.0, 0.0, 1.0, 1.0, 0.0, 1.

In [ ]:
print(len(test_targets))
print(len(test_outputs))

7063
7063


In [ ]:
test_outputs = thresholded_output_trans(test_outputs)
test_targets = thresholded_output_trans(test_targets)
print(test_outputs )
print(test_targets )

[[0, 1, 1, 0, 0, 0, 0, 0], [0, 1, 0, 0, 0, 0, 0, 0], [1, 1, 0, 0, 0, 0, 0, 0], [1, 1, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 1, 0, 0], [1, 1, 0, 0, 0, 0, 0, 0], [0, 1, 1, 0, 0, 0, 0, 0], [0, 0, 0, 0, 1, 0, 0, 0], [1, 0, 0, 1, 0, 0, 0, 0], [1, 0, 0, 0, 0, 0, 0, 0], [0, 1, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 1, 0, 0, 0], [0, 0, 0, 0, 1, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 1, 0, 0, 0], [1, 1, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 1, 0, 0, 0], [0, 0, 0, 0, 1, 0, 0, 0], [1, 0, 0, 0, 0, 0, 0, 0], [0, 1, 1, 0, 0, 0, 0, 0], [1, 0, 1, 0, 0, 0, 0, 0], [0, 0, 0, 0, 1, 0, 0, 0], [0, 0, 0, 0, 1, 0, 0, 0], [0, 0, 0, 1, 1, 0, 1, 0], [0, 1, 0, 0, 0, 0, 0, 0], [1, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 1, 0, 0, 0], [0, 0, 0, 0, 0, 1, 0, 0], [1, 1, 0, 0, 0, 0, 0, 0], [0, 0, 0, 1, 1, 0, 0, 0], [0, 0, 0, 1, 1, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 1, 0, 0, 0, 0, 0], [1, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 1, 0, 0, 0], [0, 1, 0, 0, 0, 0, 0, 0], [0, 1, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 1, 0, 0, 0], [0, 0, 0, 0

In [ ]:
print(metrics.accuracy_score(test_targets, test_outputs),metrics.f1_score(test_targets, test_outputs, average='micro'))

0.8044740195384398 0.9075229543955765


In [ ]:
eval_dataset = CustomDataset(eval_df, tokenizer, MAX_LEN)

In [ ]:
eval_data_loader = torch.utils.data.DataLoader(eval_dataset, 
    batch_size=EVAL_BATCH_SIZE,
    shuffle=True,
    num_workers=0
)

eval_targets=[]
eval_outputs=[]

In [ ]:
print('############# Eval Start   #############')
    ######################    
    # Evaluate the model #
    ######################

model.eval()
   
with torch.no_grad():
  for batch_idx, data in enumerate(eval_data_loader, 0):
    ids = data['input_ids'].to(device, dtype = torch.long)
    mask = data['attention_mask'].to(device, dtype = torch.long)
    token_type_ids = data['token_type_ids'].to(device, dtype = torch.long)
    targets = data['targets'].to(device, dtype = torch.float)
    outputs = model(ids, mask, token_type_ids)

    loss = loss_fn(outputs, targets)
    #valid_loss = valid_loss + ((1 / (batch_idx + 1)) * (loss.item() - valid_loss))
    eval_targets.extend(targets.cpu().detach().numpy().tolist())
    eval_outputs.extend(torch.sigmoid(outputs).cpu().detach().numpy().tolist())



print('############# Eval End     #############')

############# Eval Start   #############
############# Eval End     #############


In [ ]:
print(eval_targets)
print(eval_outputs)
print(len(eval_targets))
print(len(eval_outputs))

[[0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0], [0.0, 1.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0], [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0], [1.0, 0.0, 1.0, 1.0, 0.0, 0.0, 0.0, 0.0], [0.0, 0.0, 1.0, 1.0, 0.0, 0.0, 0.0, 0.0], [0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0], [1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0], [1.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0], [0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0], [0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0], [0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0], [0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0], [0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0], [0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0], [0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0], [0.0, 0.0, 0.0, 1.0, 1.0, 0.0, 0.0, 0.0], [0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0], [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0], [1.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0], [1.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0], [0.0, 0.0, 1.0, 0.0, 1.0, 0.0, 0.0, 0.0], [0.0, 1.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0], [1.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0], [1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.

In [ ]:
eval_outputs = thresholded_output_trans(eval_outputs)
eval_targets = thresholded_output_trans(eval_targets)
print(eval_outputs )
print(eval_targets )

[[0, 1, 0, 0, 0, 0, 0, 0], [1, 1, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 1, 0, 0, 0], [0, 0, 1, 1, 0, 0, 0, 0], [0, 0, 1, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 1, 0, 0], [1, 0, 0, 0, 0, 0, 0, 0], [0, 1, 1, 0, 0, 0, 0, 0], [0, 0, 1, 0, 0, 0, 0, 0], [0, 0, 0, 0, 1, 0, 0, 0], [0, 1, 1, 0, 0, 0, 0, 0], [0, 1, 1, 0, 0, 0, 0, 0], [0, 1, 1, 0, 0, 0, 0, 0], [0, 1, 1, 0, 0, 0, 0, 0], [0, 1, 1, 0, 0, 0, 0, 0], [1, 0, 0, 0, 1, 0, 0, 0], [1, 0, 1, 0, 0, 0, 0, 0], [0, 0, 1, 0, 0, 0, 0, 0], [0, 1, 1, 0, 0, 0, 0, 0], [1, 0, 0, 0, 0, 0, 0, 0], [0, 1, 1, 0, 0, 0, 0, 0], [0, 1, 1, 0, 0, 0, 0, 0], [1, 0, 0, 0, 0, 0, 0, 0], [1, 0, 0, 0, 1, 0, 0, 0], [0, 1, 1, 0, 0, 0, 0, 0], [0, 0, 1, 0, 0, 0, 0, 0], [0, 0, 0, 0, 1, 0, 0, 0], [0, 1, 0, 0, 0, 0, 0, 0], [1, 1, 0, 0, 0, 0, 0, 0], [0, 0, 1, 0, 0, 0, 0, 0], [0, 1, 1, 0, 0, 0, 0, 0], [0, 1, 1, 0, 0, 0, 0, 0], [0, 1, 1, 0, 0, 0, 0, 0], [1, 1, 1, 0, 0, 0, 0, 0], [0, 1, 1, 0, 0, 0, 0, 0], [0, 1, 1, 0, 0, 0, 0, 0], [0, 0, 1, 0, 0, 0, 0, 0], [0, 0, 1, 0, 0, 0, 0, 0], [0, 1, 1, 0

In [ ]:
print(metrics.accuracy_score(eval_targets, eval_outputs),metrics.f1_score(eval_targets, eval_outputs, average='micro'))

0.33 0.6821192052980133
